# Belousov-Zhabotinsky reaction

A Belousov-Zhabotinsky reaction simulated by a simple cellular automaton.

This reaction is one of a class of reactions that serve as a classical example of non-equilibrium thermodynamics, resulting in the establishment of a nonlinear chemical oscillator [1].

[1] http://en.wikipedia.org/wiki/Belousov-Zhabotinsky_reaction


## Imports and setup

In [ ]:
%matplotlib notebook
import time
import numpy as np
import matplotlib.pyplot as plt

plt.close('all')

np.set_printoptions(threshold=1000)

## Transition function

Here we describe simple rules for transiting from state $s^n$ to state $s^{n+1}$ that lead to results similar to the BZ reaction.

Notation:

- $s^n(i,j)$: state in step $n$ and position $(i, j)$
- $N$: n_level-1
- $c_s$: spread_limit
- $c_m$: min_contagious

The cells are in a 2D grid, each cell has 8 neighbours.

- cells with $s^n(i,j) = 0$ are *resting*
- cells with $s^n(i,j) = N$ are *contagious*
- count countagious neighbours of each cell -> $c(i, j)$
- new state for non-resting cells: $s^{n+1}(i, j) = s^{n}(i, j) - 1$
- new state for resting cells, where $c(i, j) \geq c_m$: $s^{n+1}(i, j) = N$ if random$(i, j) < c_s$
- new state for resting cells, where $c(i, j) < c_m$: $s^n(i,j) = 0$

In [ ]:
def make_bzr_step(state, n_level, min_contagious, spread_limit,
                  bc_type='death'):
    """
    The transition function, that performs single step of the
    Belousov-Zhabotinsky reaction-like cellular automaton.
    """
    n_row, n_col = state.shape

    # Get neighbour indices for all cells according to boundary conditions.
    if bc_type == 'death':
        ir0 = np.arange(0, n_row - 2)[:, None]
        ir1 = ir0 + 1
        ir2 = ir1 + 1

        ic0 = np.arange(0, n_col - 2)
        ic1 = ic0 + 1
        ic2 = ic1 + 1

        irs = slice(1, -1)
        ics = slice(1, -1)

    elif bc_type == 'periodic':
        ir1 = np.arange(0, n_row)[:, None]
        ir0 = np.roll(ir1, 1)
        ir2 = np.roll(ir1, -1)

        ic1 = np.arange(0, n_col)
        ic0 = np.roll(ic1, 1)
        ic2 = np.roll(ic1, -1)

        irs = slice(0, None)
        ics = slice(0, None)

    else:
        raise ValueError('unknown BC type! (%s)' % bc_type)

    if not state.any():
        return

    new_state = state.copy()

    # Make a view to the active part of the grid.
    active = state[irs, ics]
    new_active = new_state[irs, ics]

    resting = active == 0
    contagious = (state == (n_level - 1)).astype(np.int8)

    # Count neighbours.
    nn = contagious[ir0, ic0] + contagious[ir0, ic1] + contagious[ir0, ic2] + \
         contagious[ir1, ic0] +                    0 + contagious[ir1, ic2] + \
         contagious[ir2, ic0] + contagious[ir2, ic1] + contagious[ir2, ic2]
    
    new = resting * (nn >= min_contagious)

    random = np.random.rand(*new_active.shape)

    new_active[:, :] = (n_level - 1) * (random < spread_limit) * new + \
                       ((~resting) * (active - 1))

#     m = np.array([[1, 1, 1], [1, 0, 1], [1, 1, 1]])
#     from scipy.signal import convolve2d
#     if bc_type == 'death':
#         nn2 = convolve2d(contagious, m, mode='valid', boundary='pad')

#     elif bc_type == 'periodic':
#         nn2 = convolve2d(contagious, m, mode='same', boundary='wrap')

#     else:
#         raise ValueError('unknown BC type! (%s)' % bc_type)

#     if not ((nn2 == nn).all()):
#         print(contagious.astype(int))
#         print(nn)
#         print(nn2)
#         import pdb; pdb.set_trace()

    return new_state


## Draw state

In [ ]:
def plot_bzr_animation(image, state, n_level, min_contagious, spread_limit,
                       bc_type, pause=0.0):
    """
    Animate the Belousov-Zhabotinsky reaction.
    """
    fig = plt.gcf()

    label = plt.title('iteration 0')

    ii = 0
    while 1:
        state = make_bzr_step(state, n_level, min_contagious, spread_limit,
                              bc_type)
        if state is None:
            return
        
        image.set_data(state)

        ii += 1
        label.set_text('iteration %d' % ii)

        fig.canvas.draw()
        time.sleep(pause)
        yield True


## Simulation parameters

    n_level : int
        The number of state levels.
    min_contagious : int
        The minimum number of contagious neighbours sufficient for
        spread attempt.
    spread_limit : float in [0, 1]
        The upper limit of a random throw leading to spread.
    bc_type : 'death' or 'periodic'
        The boundary condition type.


In [ ]:
# Grid dimensions.
n_row = 400
n_col = 400

n_level = 20
min_contagious = 1
spread_limit = 0.6

# Boundary conditions ('death' or 'periodic').
#bc_type = 'death'
bc_type = 'periodic'

# Slow down animation.
pause = 0.0

## Initialization

In [ ]:
state = np.floor(n_level * np.random.rand(n_row, n_col)).astype(np.int32)

if bc_type == 'death':
    state[0, :] = 0
    state[-1, :] = 0
    state[:, 0] = 0
    state[:, -1] = 0

print(state)
print(state.max())

image = plt.imshow(state)

## Animate the BZ reaction

In [ ]:
plt.figure()

image = plt.imshow(state)

for ii in plot_bzr_animation(image, state, n_level,
                             min_contagious, spread_limit,
                             bc_type, pause):
    pass